# Notes:
This visualization notebook is used to visualize the income across different suburbs in Victoria, which is used in our presentation slides. We want to prove a strong and positive correlation exists between income and rental price

In [1]:
import pandas as pd
import geopandas as gpd
import folium

LANDING_DATA_DIR = "../../data/landing"
RAW_DATA_DIR = "../../data/raw"
CURATED_DATA_DIR = "../../data/curated"
PLOT_DIR = "../../plots"

joined = gpd.read_file(f"{CURATED_DATA_DIR}/joined_for_vis.csv", 
                       GEOM_POSSIBLE_NAMES="geometry", KEEP_GEOM_COLUMNS='NO')
postcode = gpd.read_file(f"{LANDING_DATA_DIR}/postcodes/ll_gda2020/esrishape/whole_of_dataset/victoria/VMLITE")
suburb = gpd.read_file(f"{LANDING_DATA_DIR}/suburb_locations/GDA2020")
sa2 = gpd.read_file(f"{RAW_DATA_DIR}/sa2")

In [2]:
import ast
for idx, row in joined.iterrows():
    joined['coordinates'][idx] = ast.literal_eval(row['coordinates'])

/tmp/ipykernel_7669/3751856299.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  joined['coordinates'][idx] = ast.literal_eval(row['coordinates'])


In [3]:
from shapely.geometry import Point
suburb_polygons = gpd.GeoDataFrame(suburb)
joined['suburb'] = None
null_tally = 0
for idx, row in joined.iterrows():
    point = Point(row['coordinates'][1], row['coordinates'][0])
    result = suburb_polygons[suburb_polygons.geometry.contains(point)]
    if not result.empty:
        joined['suburb'][idx] = result['LOC_NAME'].values[0]
    else:
        joined['suburb'][idx] = "Null"
        null_tally += 1

/tmp/ipykernel_7669/1250875872.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  joined['suburb'][idx] = result['LOC_NAME'].values[0]
/tmp/ipykernel_7669/1250875872.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  joined['suburb'][idx] = result['LOC_NAME'].values[0]
/tmp/ipykernel_7669/1250875872.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  joined['suburb'][idx] = result['LOC_NAME'].values[0]
/tmp/ipykernel_7669/1250875872.

In [4]:
joined = joined.rename(columns={'SA2_NAME21': 'sa2', 'price_per_week':'Rent'})
sa2 = sa2.rename(columns={'SA2_NAME21': 'sa2'})
postcode = postcode.rename(columns={'POSTCODE': 'postcode'})
suburb = suburb.rename(columns={'LOC_NAME': 'suburb'})

In [5]:
sa2_json = sa2[['sa2', 'geometry']].drop_duplicates().dropna().to_json()
suburb_json = suburb[['suburb', 'geometry']].drop_duplicates().dropna().to_json()
postcode_json = postcode[['postcode', 'geometry']].drop_duplicates().dropna().to_json()

/tmp/ipykernel_7669/2335209176.py:1: UserWarning: GeoDataFrame's CRS is not representable in URN OGC format. Resulting JSON will contain no CRS information.
  sa2_json = sa2[['sa2', 'geometry']].drop_duplicates().dropna().to_json()


In [6]:
def mapper(feature, grain):
    if grain == 'sa2':
        temp = joined[[grain, feature]].drop_duplicates().dropna()
        temp[feature] = pd.to_numeric(temp[feature], errors='coerce')
        if feature == 'Rent':
            temp = temp.groupby(grain)[feature].mean().reset_index()
        json = sa2_json
    elif grain == 'postcode':
        temp = joined[[grain, feature]].drop_duplicates().dropna()
        temp[feature] = pd.to_numeric(temp[feature], errors='coerce')
        temp = temp.groupby(grain)[feature].mean().reset_index()
        json = postcode_json
    elif grain == 'suburb':
        temp = joined[[grain, feature]].drop_duplicates().dropna()
        temp[feature] = pd.to_numeric(temp[feature], errors='coerce')
        json = suburb_json
    
    map = folium.Map(location=[-37.8136, 144.9631], tiles="Stamen Terrain", zoom_start=6)
    
    map.add_child(folium.Choropleth(
    geo_data=json,
    data=temp,
    columns=[grain, feature],
    key_on=f'feature.properties.{grain}',
    name='choropleth',
    fill_color = 'OrRd',
    fill_opacity=0.7,
    line_opacity=0.2,
    nan_fill_color='white',
    ))
    
    return map

In [7]:
mapper('Population', 'postcode')

In [9]:
pop_pos = population_mapper('postcode')
pop_sa2 = population_mapper('sa2')
pop_sub = population_mapper('suburb')

pop_pos.save(f'{PLOT_DIR}/pop_pos.html')
pop_sa2.save(f'{PLOT_DIR}/pop_sa2.html')
pop_sub.save(f'{PLOT_DIR}/pop_sub.html')